In [36]:
!pip3 install tqdm

You should consider upgrading via the '/Users/alokhegde/major_project/venvv/bin/python3 -m pip install --upgrade pip' command.


In [37]:
import pandas as pd

df = pd.read_csv("rehab24_6/Segmentation.csv")


df.head()


video_id;repetition_number;exercise_id;person_id;first_frame;last_frame;cam17_orientation;mocap_erroneous;exercise_subtype;lights_on;extra_person_in_cam17;extra_person_in_cam18;correctness
0     PM_000;1;1;1;180;377;front;0;right arm;0;3;0;1                                                                                                                                          
1     PM_000;2;1;1;378;620;front;0;right arm;0;3;0;1                                                                                                                                          
2     PM_000;3;1;1;621;865;front;0;right arm;0;3;0;1                                                                                                                                          
3    PM_000;4;1;1;866;1085;front;0;right arm;0;3;3;1                                                                                                                                          
4   PM_000;5;1;1;1086;1265;front;0;right arm;0;3;3;1

In [38]:
# The CSV is delimited by semicolons, so reload with sep=";"
df = pd.read_csv("rehab24_6/Segmentation.csv", sep=";")
a=df.groupby("exercise_id")


In [39]:

def calculate_angle(p1, p2, p3):
    p1, p2, p3 = np.array(p1), np.array(p2), np.array(p3)
    v1, v2 = p1 - p2, p3 - p2
    cosine = np.dot(v1, v2) / (np.linalg.norm(v1) * np.linalg.norm(v2))
    angle = np.degrees(np.arccos(np.clip(cosine, -1.0, 1.0)))
    return angle

def get_joint_angles(keypoints):
    angles = {}
    try:
        if all(keypoints[[5, 7, 9], 2] > 0.5):  # left elbow
            angles["left_elbow"] = calculate_angle(keypoints[5,:2], keypoints[7,:2], keypoints[9,:2])
        if all(keypoints[[6, 8, 10], 2] > 0.5):  # right elbow
            angles["right_elbow"] = calculate_angle(keypoints[6,:2], keypoints[8,:2], keypoints[10,:2])
        if all(keypoints[[11, 13, 15], 2] > 0.5):  # left knee
            angles["left_knee"] = calculate_angle(keypoints[11,:2], keypoints[13,:2], keypoints[15,:2])
        if all(keypoints[[12, 14, 16], 2] > 0.5):  # right knee
            angles["right_knee"] = calculate_angle(keypoints[12,:2], keypoints[14,:2], keypoints[16,:2])
        if all(keypoints[[11, 5, 7], 2] > 0.5):  # left shoulder
            angles["left_shoulder"] = calculate_angle(keypoints[11,:2], keypoints[5,:2], keypoints[7,:2])
        if all(keypoints[[12, 6, 8], 2] > 0.5):  # right shoulder
            angles["right_shoulder"] = calculate_angle(keypoints[12,:2], keypoints[6,:2], keypoints[8,:2])
        if all(keypoints[[5, 11, 13], 2] > 0.5):  # left hip
            angles["left_hip"] = calculate_angle(keypoints[5,:2], keypoints[11,:2], keypoints[13,:2])
        if all(keypoints[[6, 12, 14], 2] > 0.5):  # right hip
            angles["right_hip"] = calculate_angle(keypoints[6,:2], keypoints[12,:2], keypoints[14,:2])
    except:
        pass
    return angles


In [49]:
import cv2
import pandas as pd
import numpy as np
import joblib
from ultralytics import YOLO
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
import os
from tqdm import tqdm

model = YOLO("yolov8n-pose.pt")


for ex_id, group in df.groupby("exercise_id"):
    print(f"ex_id: {ex_id}")
    print(group.head())
    print(f"\n Training for exercise_id {ex_id} ...")

    data_rows = []

    for _, row in group.iterrows():
        video_id = row["video_id"]  # Already formatted as PM_000, PM_001, etc.
        
        # Try both Camera17 and Camera18
        camera_options = [
            f"/Users/alokhegde/major_project/rehab24_6/videos/Ex1/{video_id}-Camera17-30fps.mp4",
        ]
        
        video_path = None
        for path in camera_options:
            if os.path.exists(path):
                video_path = path
                break
        
        if video_path is None:
            print(f"Video not found for {video_id} in Ex{ex_id}")
            continue
        
        print(f"Using: {video_path}")

        first_frame = int(row["first_frame"])
        last_frame = int(row["last_frame"])
        mid_frame = (first_frame + last_frame) // 2
        print('mid frame',mid_frame)
        cap = cv2.VideoCapture(video_path)
        cap.set(cv2.CAP_PROP_POS_FRAMES, mid_frame)
        ret, frame = cap.read()
        cap.release()
        
        if not ret:
            print(f"Failed to read frame from {video_path}")
            continue

        results = model(frame, verbose=False)
        keypoints = results[0].keypoints.data.cpu().numpy()[0]
        angles = get_joint_angles(keypoints)

        if len(angles) < 3:
            continue

        angles["correctness"] = int(row["correctness"])
        data_rows.append(angles)
        print(data_rows)
        

   

  
    


ex_id: 1
  video_id  repetition_number  exercise_id  person_id  first_frame  \
0   PM_000                  1            1          1          180   
1   PM_000                  2            1          1          378   
2   PM_000                  3            1          1          621   
3   PM_000                  4            1          1          866   
4   PM_000                  5            1          1         1086   

   last_frame cam17_orientation  mocap_erroneous exercise_subtype  lights_on  \
0         377             front                0        right arm          0   
1         620             front                0        right arm          0   
2         865             front                0        right arm          0   
3        1085             front                0        right arm          0   
4        1265             front                0        right arm          0   

   extra_person_in_cam17  extra_person_in_cam18  correctness  
0                      3  

In [51]:
print(data_rows)

[]


In [ ]:
  ex_df = pd.DataFrame(data_rows).fillna(0)

    # =============================================
    # 5️⃣  Train classifier
    # =============================================
    X = ex_df.drop(columns=["correctness"])
    y = ex_df["correctness"]

    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

    clf = RandomForestClassifier(n_estimators=100, random_state=42)
    clf.fit(X_train, y_train)
    acc = accuracy_score(y_test, clf.predict(X_test))
    print(f"Accuracy for exercise {ex_id}: {acc:.2f}")

    joblib.dump(clf, f"models/model_ex{ex_id}.pkl")
    print(f"Saved model_ex{ex_id}.pkl")

In [54]:
import pandas as pd

df = pd.read_csv("rehab24_6/Segmentation.csv", sep=";")


# Check what the CSV says about PM_000
pm_000_data = df[df['video_id'] == 'PM_000']
print("Ground truth for PM_000:")
print(pm_000_data[['video_id', 'exercise_id', 'repetition_number', 'correctness', 'first_frame', 'last_frame']])
print(f"\nTotal rows: {len(pm_000_data)}")
print(f"Correct (1): {len(pm_000_data[pm_000_data['correctness'] == 1])}")
print(f"Incorrect (0): {len(pm_000_data[pm_000_data['correctness'] == 0])}")

Ground truth for PM_000:
  video_id  exercise_id  repetition_number  correctness  first_frame  \
0   PM_000            1                  1            1          180   
1   PM_000            1                  2            1          378   
2   PM_000            1                  3            1          621   
3   PM_000            1                  4            1          866   
4   PM_000            1                  5            1         1086   

   last_frame  
0         377  
1         620  
2         865  
3        1085  
4        1265  

Total rows: 5
Correct (1): 5
Incorrect (0): 0


In [55]:
import joblib
import pandas as pd

# Load the model
clf = joblib.load("models/model_ex1.pkl")

# Check model details
print("\n🔍 Model Information:")
print(f"Model type: {type(clf)}")
if hasattr(clf, 'n_estimators'):
    print(f"Number of estimators: {clf.n_estimators}")

print(f"\n📊 Feature names expected by model:")
if hasattr(clf, 'feature_names_in_'):
    print(clf.feature_names_in_)

print(f"\n📈 Feature importances:")
if hasattr(clf, 'feature_importances_'):
    features = clf.feature_names_in_ if hasattr(clf, 'feature_names_in_') else range(len(clf.feature_importances_))
    for feat, imp in zip(features, clf.feature_importances_):
        print(f"  {feat}: {imp:.4f}")

# Check class distribution
if hasattr(clf, 'classes_'):
    print(f"\n🎯 Classes: {clf.classes_}")


🔍 Model Information:
Model type: <class 'sklearn.ensemble._forest.RandomForestClassifier'>
Number of estimators: 100

📊 Feature names expected by model:
['left_elbow' 'right_elbow' 'left_knee' 'right_knee' 'left_shoulder' 'right_shoulder' 'left_hip' 'right_hip']

📈 Feature importances:
  left_elbow: 0.1072
  right_elbow: 0.1480
  left_knee: 0.1169
  right_knee: 0.0949
  left_shoulder: 0.1369
  right_shoulder: 0.1608
  left_hip: 0.1263
  right_hip: 0.1089

🎯 Classes: [0 1]


In [1]:
!pip install openai

  Using cached openai-2.8.1-py3-none-any.whl (1.0 MB)
     |████████████████████████████████| 463 kB 3.3 MB/s eta 0:00:01
  Using cached distro-1.9.0-py3-none-any.whl (20 kB)
  Using cached sniffio-1.3.1-py3-none-any.whl (10 kB)
  Using cached httpx-0.28.1-py3-none-any.whl (73 kB)
  Using cached jiter-0.12.0-cp39-cp39-macosx_11_0_arm64.whl (312 kB)
     |████████████████████████████████| 113 kB 12.3 MB/s eta 0:00:01
  Using cached httpcore-1.0.9-py3-none-any.whl (78 kB)
  Using cached h11-0.16.0-py3-none-any.whl (37 kB)
  Using cached pydantic_core-2.41.5-cp39-cp39-macosx_11_0_arm64.whl (1.9 MB)
  Using cached typing_inspection-0.4.2-py3-none-any.whl (14 kB)
  Using cached annotated_types-0.7.0-py3-none-any.whl (13 kB)
You should consider upgrading via the '/Users/alokhegde/major_project/venvv/bin/python3 -m pip install --upgrade pip' command.


In [5]:
import openai
import os

openai.api_key = os.getenv("OPENAI_API_KEY")

import json

def get_exercise_feedback_from_gpt(json_filepath, openai_model="gpt-3.5-turbo"):
    with open(json_filepath, "r") as f:
        exercise_data = json.load(f)

    prompt = (
        "You are an expert exercise assessor. Given the following user exercise data in JSON, analyze the performance. "
        "Explain in natural language where the person is going wrong, based on the statistics and any per-rep breakdowns. "
        "Be concise, actionable, and point out common error phases, incorrect reps, or likely issues. "
        "If there are arm-specific statistics or phases (e.g. ascent/descent), mention those. "
        "Here is the exercise data:\n\n"
        f"{json.dumps(exercise_data, indent=2)}\n\n"
        "Provide a summary of the mistakes or places for improvement."
    )

    response = openai.chat.completions.create(
        model=openai_model,
        messages=[
            {"role": "system", "content": "You are a knowledgeable exercise performance analyst."},
            {"role": "user", "content": prompt}
        ],
        max_tokens=400
    )

    feedback = response.choices[0].message.content
    return feedback


# Example usage (make sure OPENAI_API_KEY is set):
feedback = get_exercise_feedback_from_gpt("exercise_data.json")
print("GPT feedback:\n", feedback)



GPT feedback:
 Based on the exercise data provided for the Shoulder Raise:

1. Right Arm Analysis:
   - The user completed 4 out of 5 target reps with good overall form.
   - Repetitions 1 had a moderate form breakdown during the descent phase.
   - Repetitions 2-4 were performed excellently with only mild issues during descent.
   - The common error phase identified was during the descent.
   - The user should focus on maintaining control during the descent phase to improve form consistency.

2. Left Arm Analysis:
   - The user did not complete any reps with the left arm, resulting in a form ratio of 0.0.

3. Overall Assessment:
   - The exercise completion status was partial due to incomplete reps with the left arm.
   - The overall form rating was Excellent for the completed reps with the right arm.
   - Primary recommendation: Focus on controlled lowering of the arm to maintain form during the descent phase.
   - Additional recommendation: Aim for fuller arm extension to achieve hi

In [ ]:
from openai import AsyncOpenAI

# Set API key
client = AsyncOpenAI(api_key=os.getenv("OPENAI_API_KEY"))
import asyncio

async def ask_tallest_building_in_india():
    response = await client.chat.completions.create(
        model="gpt-4o-mini",
        messages=[
            {"role": "system", "content": "You are a helpful assistant."},
            {"role": "user", "content": "What is the tallest building in India?"}
        ],
        max_tokens=100
    )
    answer = response.choices[0].message.content
    print("Tallest building in India:", answer)



RuntimeError: asyncio.run() cannot be called from a running event loop